In [1]:
import pandas as pd 
import numpy as np
from latex_table import generate_table, generate_rows
import matplotlib.pyplot as plt
from matplotlib.ticker import FormatStrFormatter

class WandBWrapper:
    def __init__(self, prefix=''):
        import wandb
        self.api = wandb.Api()
        self.prefix = prefix
    
    def get_runs(self, name):
        return self.api.runs(f"{self.prefix}{name}")
    
    def _preprocess_config(self, run):
        return {
            k: v for k,v in run.config.items()
            if not k.startswith('_')
        }
    
    def _best_in_history(self, run, key):
        out = run.history()[key].astype('float').fillna(0).max()
        return max(out, 0)
    
    def get_full_history(self, runs, tasks, model_size=''):
        task_names = [model_size + '_' + task_name for task_name in tasks]
        return {
            task_name: pd.DataFrame({
                run.name: run.history()['valid_mean']
                for run in self.get_runs(task_name)
                if run.name in runs
            })[runs]
            for task_name in task_names
        }
    
    def get_runs_best(self, name, run_name_filter=None):
        runs = self.get_runs(name)
        return {
            run.name: self._best_in_history(run, 'valid_mean')
            for run in runs
            if run_name_filter is None or run.name in run_name_filter
        }
    
    def get_runs_tasks_df(self, runs, tasks, model_size=''):
        task_names = [model_size + '_' + task_name for task_name in tasks]
        results = {task_name: self.get_runs_best(task_name, runs) for task_name in task_names}
        return pd.DataFrame(results).T[runs].T

In [4]:
tasks = [
    # 'glue-wnli',
    # 'glue-rte',
    'glue-qqp',  # new datasets
    # 'glue-qnli', # new datasets
    # 'glue-mnli', # new datasets
    # 'glue-sst2', # new datasets
    # 'glue-stsb', # new datasets
    'glue-mrpc',
    'glue-cola',
    # 'superglue-multirc', # new datasets
    'superglue-rte',
    'superglue-cb',
    # 'superglue-copa', # not in attempt
    'superglue-wic',
    'superglue-boolq',
]

runs = [
    '10_combine_128',
]

df =  WandBWrapper("mohalisad/iclr_orig_t5_t5_").get_runs_tasks_df(
    runs=runs,
    tasks=tasks,
    model_size='base'
)

In [5]:
df

base_glue-qqp  base_glue-mrpc  base_glue-cola  \
10_combine_128       0.892432        0.909251        0.596682   

                base_superglue-rte  base_superglue-cb  base_superglue-copa  \
10_combine_128            0.801444           0.968944                 0.66   

                base_superglue-wic  base_superglue-boolq  
10_combine_128            0.675549              0.813456